<a href="https://colab.research.google.com/github/internptikb/tts-telemarketing/blob/main/nb/Sesame_CSM_(1B)-TTS.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

To run this, press "*Runtime*" and press "*Run all*" on a **free** Tesla T4 Google Colab instance!
<div class="align-center">
<a href="https://unsloth.ai/"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
<a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord button.png" width="145"></a>
<a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a></a> Join Discord if you need help + ⭐ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐
</div>

To install Unsloth on your own computer, follow the installation instructions on our Github page [here](https://docs.unsloth.ai/get-started/installing-+-updating).

You will learn how to do [data prep](#Data), how to [train](#Train), how to [run the model](#Inference), & [how to save it](#Save)


### News

Unsloth now supports Text-to-Speech (TTS) models. Read our [guide here](https://docs.unsloth.ai/basics/text-to-speech-tts-fine-tuning).

Read our **[Gemma 3N Guide](https://docs.unsloth.ai/basics/gemma-3n-how-to-run-and-fine-tune)** and check out our new **[Dynamic 2.0](https://docs.unsloth.ai/basics/unsloth-dynamic-2.0-ggufs)** quants which outperforms other quantization methods!

Visit our docs for all our [model uploads](https://docs.unsloth.ai/get-started/all-our-models) and [notebooks](https://docs.unsloth.ai/get-started/unsloth-notebooks).


### Installation

In [1]:
%%capture
import os
if "COLAB_" not in "".join(os.environ.keys()):
    !pip install unsloth
else:
    # Do this only in Colab notebooks! Otherwise use pip install unsloth
    !pip install --no-deps bitsandbytes accelerate xformers==0.0.29.post3 peft trl triton cut_cross_entropy unsloth_zoo
    !pip install sentencepiece protobuf "datasets>=3.4.1,<4.0.0" "huggingface_hub>=0.34.0" hf_transfer
    !pip install --no-deps unsloth
!pip install transformers==4.52.3

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


### Unsloth

`FastModel` supports loading nearly any model now! This includes Vision and Text models!

In [3]:
from unsloth import FastModel
from transformers import CsmForConditionalGeneration
import torch

model, processor = FastModel.from_pretrained(
    model_name = "unsloth/csm-1b",
    max_seq_length= 2048, # Choose any for long context!
    dtype = None, # Leave as None for auto-detection
    auto_model = CsmForConditionalGeneration,
    load_in_4bit = False, # Select True for 4bit - reduces memory usage
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!
==((====))==  Unsloth 2025.8.1: Fast Csm patching. Transformers: 4.52.3.
   \\   /|    NVIDIA L4. Num GPUs = 1. Max memory: 22.161 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 8.9. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = TRUE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: QLoRA and full finetuning all not selected. Switching to 16bit LoRA.


model.safetensors:   0%|          | 0.00/4.15G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/264 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json:   0%|          | 0.00/17.2M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/449 [00:00<?, ?B/s]

chat_template.jinja: 0.00B [00:00, ?B/s]

unsloth/csm-1b does not have a padding token! Will use pad_token = <|PAD_TOKEN|>.


We now add LoRA adapters so we only need to update 1 to 10% of all parameters!

In [4]:
model = FastModel.get_peft_model(
    model,
    r = 32, # Choose any number > 0 ! Suggested 8, 16, 32, 64, 128
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj",],
    lora_alpha = 32,
    lora_dropout = 0, # Supports any, but = 0 is optimized
    bias = "none",    # Supports any, but = "none" is optimized
    # [NEW] "unsloth" uses 30% less VRAM, fits 2x larger batch sizes!
    use_gradient_checkpointing = "unsloth", # True or "unsloth" for very long context
    random_state = 3407,
    use_rslora = False,  # We support rank stabilized LoRA
    loftq_config = None, # And LoftQ
)

Unsloth: Making `model.base_model.model.backbone_model` require gradients


<a name="Data"></a>
### Data Prep  

We will use the `MrDragonFox/Elise`, which is designed for training TTS models. Ensure that your dataset follows the required format: **text, audio** for single-speaker models or **source, text, audio** for multi-speaker models. You can modify this section to accommodate your own dataset, but maintaining the correct structure is essential for optimal training.

In [46]:
#@title Dataset Prep functions with Fixed Audio Length
import os
from datasets import load_dataset, Audio, Dataset
from transformers import AutoProcessor
import torch
import numpy as np

# --- START OF CORRECTIONS ---
# 1. Define the base path where your metadata.csv and wavs folder are located.
base_path = "drive/MyDrive/DatasetIKB/TeleData/"
metadata_path = os.path.join(base_path, "metadata.csv")
print(f"Base path set to: {base_path}")
print(f"Metadata path set to: {metadata_path}")

# 2. Load the dataset. The 'audio' column will initially contain the relative paths.
print("Loading dataset from CSV file")
try:
    raw_ds = load_dataset("csv", data_files=metadata_path, split="train")
    print(f"Dataset loaded successfully. Number of examples: {len(raw_ds)}")
    print(f"Dataset columns: {raw_ds.column_names}")
    print(f"First example: {raw_ds[0]}")
except Exception as e:
    print(f"Error loading dataset: {e}")
    raise

# 3. Create a function to make the file paths absolute.
def make_path_absolute(example):
    original_path = example["audio"]
    absolute_path = os.path.join(base_path, example["audio"])
    example["audio"] = absolute_path
    print(f"Converted path from {original_path} to {absolute_path}")
    if not os.path.exists(absolute_path):
        print(f"Warning: Audio file does not exist: {absolute_path}")
    return example

# 4. Apply the function to the entire dataset to fix all the paths.
print("Applying absolute path conversion to dataset")
try:
    raw_ds = raw_ds.map(make_path_absolute, desc="Converting to absolute paths")
    print("Path conversion completed successfully")
except Exception as e:
    print(f"Error during path conversion: {e}")
    raise

# Cast audio column to specified sampling rate
target_sampling_rate = 24000
print(f"Casting audio column to sampling rate: {target_sampling_rate}")
try:
    raw_ds = raw_ds.cast_column("audio", Audio(sampling_rate=target_sampling_rate))
    print("Audio column casting completed")
except Exception as e:
    print(f"Error casting audio column: {e}")
    raise

# Load processor
print("Loading AutoProcessor from 'unsloth/csm-1b'")
try:
    processor = AutoProcessor.from_pretrained("unsloth/csm-1b")
    print("Processor loaded successfully")
except Exception as e:
    print(f"Error loading processor: {e}")
    raise

# Handle speaker key
speaker_key = "source"
if "source" not in raw_ds.column_names and "speaker_id" not in raw_ds.column_names:
    print("Warning: No speaker found, adding default 'source' of 0 for all examples")
    new_column = ["0"] * len(raw_ds)
    raw_ds = raw_ds.add_column("source", new_column)
    print("Default 'source' column added")
elif "source" not in raw_ds.column_names and "speaker_id" in raw_ds.column_names:
    speaker_key = "speaker_id"
    print("Using 'speaker_id' as speaker key")
else:
    print("Using 'source' as speaker key")

# Preprocess function with manual audio truncation/padding
def preprocess_example(example):
    print(f"Preprocessing example with text: {example['text'][:50]}...")
    # Manually truncate or pad audio array to ensure consistent length
    max_audio_length = 240001
    audio_array = example["audio"]["array"]
    original_length = len(audio_array)
    if original_length > max_audio_length:
        print(f"Warning: Audio array length {original_length} exceeds max_length {max_audio_length}, truncating")
        audio_array = audio_array[:max_audio_length]
    elif original_length < max_audio_length:
        print(f"Info: Audio array length {original_length} is less than max_length {max_audio_length}, padding")
        audio_array = np.pad(audio_array, (0, max_audio_length - original_length), mode='constant')
    print(f"Adjusted audio array length: {len(audio_array)}")

    conversation = [
        {
            "role": str(example[speaker_key]),
            "content": [
                {"type": "text", "text": example["text"]},
                {"type": "audio", "path": audio_array},
            ],
        }
    ]
    try:
        model_inputs = processor.apply_chat_template(
            conversation,
            tokenize=True,
            return_dict=True,
            output_labels=True,
            text_kwargs={
                "padding": "max_length",
                "max_length": 256,
                "pad_to_multiple_of": 8,
                "padding_side": "right",
            },
            audio_kwargs={
                "sampling_rate": 24_000,
                "max_length": 240001,
                "padding": "max_length",
            },
            common_kwargs={"return_tensors": "pt"},
        )
        print(f"Processor output keys: {list(model_inputs.keys())}")
    except Exception as e:
        print(f"Error processing example with text '{example['text'][:50]}...': {e}")
        return None

    required_keys = ["input_ids", "attention_mask", "labels", "input_values", "input_values_cutoffs"]
    processed_example = {}
    for key in required_keys:
        if key not in model_inputs:
            print(f"Warning: Required key '{key}' not found in processor output for example")
            return None
        value = model_inputs[key][0]
        processed_example[key] = value
        print(f"Added {key} to processed example. Shape: {value.shape if isinstance(value, torch.Tensor) else 'N/A'}")

    if not all(isinstance(processed_example[key], torch.Tensor) for key in processed_example):
        print(f"Error: Not all required keys are tensors. Keys: {list(processed_example.keys())}")
        return None

    print("Example preprocessing completed successfully")
    return processed_example

# Apply preprocessing to dataset
print("Starting dataset preprocessing")
try:
    processed_ds = raw_ds.map(
        preprocess_example,
        remove_columns=raw_ds.column_names,
        desc="Preprocessing dataset",
    )
    print(f"Dataset preprocessing completed. Number of examples: {len(processed_ds)}")
    print(f"Processed dataset columns: {processed_ds.column_names}")
except Exception as e:
    print(f"Error during dataset preprocessing: {e}")
    raise

Base path set to: drive/MyDrive/DatasetIKB/TeleData/
Metadata path set to: drive/MyDrive/DatasetIKB/TeleData/metadata.csv
Loading dataset from CSV file
Dataset loaded successfully. Number of examples: 999
Dataset columns: ['audio', 'text']
First example: {'audio': 'wavs/0001.wav', 'text': 'Selamat sore Bu Berapa kisaran harga yang sesuai dengan kebutuhan Anda agar kami bisa memberikan penawaran terbaik? Mohon waktunya sebentar.'}
Applying absolute path conversion to dataset


Converting to absolute paths:   0%|          | 0/999 [00:00<?, ? examples/s]

Converted path from wavs/0001.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0001.wav
Converted path from wavs/0002.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0002.wav
Converted path from wavs/0003.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0003.wav
Converted path from wavs/0004.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0004.wav
Converted path from wavs/0005.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0005.wav
Converted path from wavs/0006.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0006.wav
Converted path from wavs/0007.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0007.wav
Converted path from wavs/0008.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0008.wav
Converted path from wavs/0009.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0009.wav
Converted path from wavs/0010.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0010.wav
Converted path from wavs/0011.wav to drive/MyDrive/DatasetIKB/TeleData/wavs/0011.wav
Converted path from wavs/0012.wav to drive/MyDrive/DatasetIKB/Tel

Preprocessing dataset:   0%|          | 0/999 [00:00<?, ? examples/s]

Streaming output truncated to the last 5000 lines.
Adjusted audio array length: 240001
Processor output keys: ['input_ids', 'attention_mask', 'input_values', 'input_values_cutoffs', 'labels']
Added input_ids to processed example. Shape: torch.Size([256])
Added attention_mask to processed example. Shape: torch.Size([256])
Added labels to processed example. Shape: torch.Size([256])
Added input_values to processed example. Shape: torch.Size([1, 240001])
Added input_values_cutoffs to processed example. Shape: torch.Size([1])
Example preprocessing completed successfully
Preprocessing example with text: Halo Kak Seberapa puas Anda dengan produk dan laya...
Info: Audio array length 176903 is less than max_length 240001, padding
Adjusted audio array length: 240001
Processor output keys: ['input_ids', 'attention_mask', 'input_values', 'input_values_cutoffs', 'labels']
Added input_ids to processed example. Shape: torch.Size([256])
Added attention_mask to processed example. Shape: torch.Size([256

<a name="Train"></a>
### Train the model
Now let's use Huggingface  `Trainer`! More docs here: [Transformers docs](https://huggingface.co/docs/transformers/main_classes/trainer). We do 60 steps to speed things up, but you can set `num_train_epochs=1` for a full run, and turn off `max_steps=None`.

In [47]:
from transformers import TrainingArguments, Trainer
from unsloth import is_bfloat16_supported

trainer = Trainer(
    model = model,
    train_dataset = processed_ds,
    args = TrainingArguments(
        per_device_train_batch_size = 2,
        gradient_accumulation_steps = 4,
        warmup_steps = 5,
        max_steps = 60,
        learning_rate = 2e-4,
        fp16 = not is_bfloat16_supported(),
        bf16 = is_bfloat16_supported(),
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        output_dir = "outputs",
        report_to = "none",
    ),
)

In [19]:
# @title Show current memory stats
gpu_stats = torch.cuda.get_device_properties(0)
start_gpu_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
max_memory = round(gpu_stats.total_memory / 1024 / 1024 / 1024, 3)
print(f"GPU = {gpu_stats.name}. Max memory = {max_memory} GB.")
print(f"{start_gpu_memory} GB of memory reserved.")

GPU = NVIDIA L4. Max memory = 22.161 GB.
6.719 GB of memory reserved.


In [44]:
print(processed_ds)
print(processed_ds[0])  # Inspect a single sample

Dataset({
    features: ['input_ids', 'attention_mask', 'labels', 'input_values', 'input_values_cutoffs'],
    num_rows: 999
})
{'input_ids': [128000, 58, 15, 60, 40141, 43011, 36366, 28326, 9084, 18826, 597, 285, 22026, 72448, 10587, 15907, 85795, 21045, 2004, 8248, 70986, 40238, 70479, 63769, 41088, 4562, 23014, 5869, 675, 22026, 2024, 4749, 1609, 30, 20409, 263, 289, 10114, 82371, 103382, 80780, 13, 128001, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 128002, 12

In [48]:
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 999 | Num Epochs = 1 | Total steps = 60
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 4 x 1) = 8
 "-____-"     Trainable parameters = 29,032,448 of 1,661,132,609 (1.75% trained)
`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.


Unsloth: Will smartly offload gradients to save VRAM!


In [49]:
# @title Show final memory and time stats
used_memory = round(torch.cuda.max_memory_reserved() / 1024 / 1024 / 1024, 3)
used_memory_for_lora = round(used_memory - start_gpu_memory, 3)
used_percentage = round(used_memory / max_memory * 100, 3)
lora_percentage = round(used_memory_for_lora / max_memory * 100, 3)
print(f"{trainer_stats.metrics['train_runtime']} seconds used for training.")
print(
    f"{round(trainer_stats.metrics['train_runtime']/60, 2)} minutes used for training."
)
print(f"Peak reserved memory = {used_memory} GB.")
print(f"Peak reserved memory for training = {used_memory_for_lora} GB.")
print(f"Peak reserved memory % of max memory = {used_percentage} %.")
print(f"Peak reserved memory for training % of max memory = {lora_percentage} %.")

233.0155 seconds used for training.
3.88 minutes used for training.
Peak reserved memory = 6.719 GB.
Peak reserved memory for training = 0.0 GB.
Peak reserved memory % of max memory = 30.319 %.
Peak reserved memory for training % of max memory = 0.0 %.


<a name="Inference"></a>
### Inference
Let's run the model! You can change the prompts

In [58]:
from IPython.display import Audio, display
import soundfile as sf

text = "Selamat pagi. Selamat siang. Selamat malam Bapak Ibu semuanya."
speaker_id = 0
inputs = processor(f"[{speaker_id}]{text}", add_special_tokens=True).to("cuda")
audio_values = model.generate(
    **inputs,
    max_new_tokens=125, # 125 tokens is 10 seconds of audio, for longer speech increase this
    # play with these parameters to tweak results
    depth_decoder_top_k=0,
    depth_decoder_top_p=0.9,
    depth_decoder_do_sample=True,
    depth_decoder_temperature=0.9,
    top_k=0,
    top_p=1.0,
    temperature=0.9,
    do_sample=True,
    #########################################################
    output_audio=True
)
audio = audio_values[0].to(torch.float32).cpu().numpy()
sf.write("example_without_context.wav", audio, 24000)
display(Audio(audio, rate=24000))

<a name="Enhanced Speech by Grok"></a>
### Enhanced Speech by Grok
Let's run the model! You can change the prompts

In [59]:
from IPython.display import Audio, display
import soundfile as sf
import torch
import numpy as np
import librosa

# Input text and speaker ID
text = "Selamat pagi. Selamat siang. Selamat malam Bapak Ibu semuanya."
speaker_id = 0  # Ensure this matches a speaker ID from your fine-tuned dataset
print(f"Generating audio for text: {text} with speaker_id: {speaker_id}")

# Create a conversational context for more natural intonation
context = (
    f"[{speaker_id}]Halo, apa kabar? Saya ingin menyapa Anda semua dengan penuh semangat! "
    f"{text}"
)
print(f"Full input with context: {context}")

# Process the input with the processor
inputs = processor(context, add_special_tokens=True).to("cuda")
print("Inputs processed and moved to CUDA")

# Generate audio with adjusted parameters for naturalness
audio_values = model.generate(
    **inputs,
    max_new_tokens=150,  # Increased to allow for longer, natural-sounding audio
    depth_decoder_top_k=50,  # Moderate top-k to balance quality and diversity
    depth_decoder_top_p=0.85,  # Slightly lower top-p for more focused sampling
    depth_decoder_do_sample=True,
    depth_decoder_temperature=0.7,  # Lower temperature for more consistent output
    top_k=50,  # Moderate top-k for main sampling
    top_p=0.9,  # Slightly lower top-p for main sampling
    temperature=0.7,  # Lower temperature for more natural-sounding results
    do_sample=True,
    output_audio=True
)
print("Audio generated successfully")

# Convert audio to numpy and apply post-processing
audio = audio_values[0].to(torch.float32).cpu().numpy()
print(f"Raw audio shape: {audio.shape}")

# Normalize audio to prevent clipping and improve loudness
audio = librosa.util.normalize(audio)
print("Audio normalized")

# Optional: Apply a simple high-pass filter to reduce low-frequency noise
audio = librosa.effects.preemphasis(audio, coef=0.97)
print("High-pass filter applied")

# Save the audio file
output_file = "example_natural_audio.wav"
sf.write(output_file, audio, 24000)
print(f"Audio saved to {output_file}")

# Display the audio
display(Audio(audio, rate=24000))
print("Audio displayed")

Generating audio for text: Selamat pagi. Selamat siang. Selamat malam Bapak Ibu semuanya. with speaker_id: 0
Full input with context: [0]Halo, apa kabar? Saya ingin menyapa Anda semua dengan penuh semangat! Selamat pagi. Selamat siang. Selamat malam Bapak Ibu semuanya.
Inputs processed and moved to CUDA
Audio generated successfully
Raw audio shape: (286080,)
Audio normalized
High-pass filter applied
Audio saved to example_natural_audio.wav


Audio displayed


In [ ]:
text = "Sesame is a super cool TTS model which can be fine tuned with Unsloth."

speaker_id = 0
# Another equivalent way to prepare the inputs
conversation = [
    {"role": str(speaker_id), "content": [{"type": "text", "text": text}]},
]
audio_values = model.generate(
    **processor.apply_chat_template(
        conversation,
        tokenize=True,
        return_dict=True,
    ).to("cuda"),
    max_new_tokens=125, # 125 tokens is 10 seconds of audio, for longer speech increase this
    # play with these parameters to tweak results
    # depth_decoder_top_k=0,
    # depth_decoder_top_p=0.9,
    # depth_decoder_do_sample=True,
    # depth_decoder_temperature=0.9,
    # top_k=0,
    # top_p=1.0,
    # temperature=0.9,
    # do_sample=True,
    #########################################################
    output_audio=True
)
audio = audio_values[0].to(torch.float32).cpu().numpy()
sf.write("example_without_context.wav", audio, 24000)
display(Audio(audio, rate=24000))

#### Voice and style consistency

Sesame CSM's power comes from providing audio context for each speaker. Let's pass a sample utterance from our dataset to ground speaker identity and style.

In [ ]:
speaker_id = 0

utterance = raw_ds[3]["audio"]["array"]
utterance_text = raw_ds[3]["text"]
text = "Sesame is a super cool TTS model which can be fine tuned with Unsloth."

# CSM will fill in the audio for the last text.
# You can even provide a conversation history back in as you generate new audio

conversation = [
    {"role": str(speaker_id), "content": [{"type": "text", "text": utterance_text},{"type": "audio", "path": utterance}]},
    {"role": str(speaker_id), "content": [{"type": "text", "text": text}]},
]

inputs = processor.apply_chat_template(
        conversation,
        tokenize=True,
        return_dict=True,
    )
audio_values = model.generate(
    **inputs.to("cuda"),
    max_new_tokens=125, # 125 tokens is 10 seconds of audio, for longer text increase this
    # play with these parameters to tweak results
    # depth_decoder_top_k=0,
    # depth_decoder_top_p=0.9,
    # depth_decoder_do_sample=True,
    # depth_decoder_temperature=0.9,
    # top_k=0,
    # top_p=1.0,
    # temperature=0.9,
    # do_sample=True,
    #########################################################
    output_audio=True
)
audio = audio_values[0].to(torch.float32).cpu().numpy()
sf.write("example_with_context.wav", audio, 24000)
display(Audio(audio, rate=24000))

<a name="Save"></a>
### Saving, loading finetuned models
To save the final model as LoRA adapters, either use Huggingface's `push_to_hub` for an online save or `save_pretrained` for a local save.

**[NOTE]** This ONLY saves the LoRA adapters, and not the full model. To save to 16bit or GGUF, scroll down!

In [ ]:
model.save_pretrained("lora_model")  # Local saving
processor.save_pretrained("lora_model")
# model.push_to_hub("your_name/lora_model", token = "...") # Online saving
# processor.push_to_hub("your_name/lora_model", token = "...") # Online saving

[]

### Saving to float16

We also support saving to `float16` directly. Select `merged_16bit` for float16 or `merged_4bit` for int4. We also allow `lora` adapters as a fallback. Use `push_to_hub_merged` to upload to your Hugging Face account! You can go to https://huggingface.co/settings/tokens for your personal tokens.

In [ ]:
# Merge to 16bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_16bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_16bit", token = "")

# Merge to 4bit
if False: model.save_pretrained_merged("model", tokenizer, save_method = "merged_4bit",)
if False: model.push_to_hub_merged("hf/model", tokenizer, save_method = "merged_4bit", token = "")

# Just LoRA adapters
if False:
    model.save_pretrained("model")
    tokenizer.save_pretrained("model")
if False:
    model.push_to_hub("hf/model", token = "")
    tokenizer.push_to_hub("hf/model", token = "")


And we're done! If you have any questions on Unsloth, we have a [Discord](https://discord.gg/unsloth) channel! If you find any bugs or want to keep updated with the latest LLM stuff, or need help, join projects etc, feel free to join our Discord!

Some other links:
1. Train your own reasoning model - Llama GRPO notebook [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.1_(8B)-GRPO.ipynb)
2. Saving finetunes to Ollama. [Free notebook](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3_(8B)-Ollama.ipynb)
3. Llama 3.2 Vision finetuning - Radiography use case. [Free Colab](https://colab.research.google.com/github/unslothai/notebooks/blob/main/nb/Llama3.2_(11B)-Vision.ipynb)
6. See notebooks for DPO, ORPO, Continued pretraining, conversational finetuning and more on our [documentation](https://docs.unsloth.ai/get-started/unsloth-notebooks)!

<div class="align-center">
  <a href="https://unsloth.ai"><img src="https://github.com/unslothai/unsloth/raw/main/images/unsloth%20new%20logo.png" width="115"></a>
  <a href="https://discord.gg/unsloth"><img src="https://github.com/unslothai/unsloth/raw/main/images/Discord.png" width="145"></a>
  <a href="https://docs.unsloth.ai/"><img src="https://github.com/unslothai/unsloth/blob/main/images/documentation%20green%20button.png?raw=true" width="125"></a>

  Join Discord if you need help + ⭐️ <i>Star us on <a href="https://github.com/unslothai/unsloth">Github</a> </i> ⭐️
</div>
